# Training on Your Private Data - by NathMath @ bilibili

大家好，这里是Nathmath。我将用一个系列给你们讲解如何基于预训练好的底模进行大语言模型的私有数据微调。
> * 区别于部分UP主，我可能会“废话”很多。但是，“废话”才是你们学习的基础。因为我的“废话”是在讲解原理，让你们`能“鱼”也能“渔”`（钓鱼），意思是懂得原理，就可以不仅仅学会这一个微调，并且能够自己用在其他需要的地方，迁移学习。而不是仅仅学会我这一个东西，无法举一反三。

> * 本系列视频特别推荐大家动手。以本期视频举例，很多同学还不会准备数据集，没事，请一定要拿我的数据先跑一遍，遍跑遍听我的讲解，理解每一步在做什么；我后面的视频会继续教你们怎么准备数据集（会的同学仅看本期就可以），以及怎么进行多轮对话训练、怎么进行思考训练、怎么进行其他模型的训练；当然，最基础的，建议大家自己`先照猫画虎把我的Notebook跑通`，然后再自己尝试自己的数据。

> * 微调和训练是很难很难的内容。包括训练数据准备。在行内，有着“`数据处理80%，建模训练20%`”的行话，意思是数据处理所消耗的时间和精力占到整个机器学习的80%，其也决定了你模型的质量的80%，因为"garbage in, garbage out"（进去的是垃圾，出来的也是垃圾）。大家`一定不要灰心`，如果想学的话，踏踏实实学，有问题就问ChatGPT/DeepSeek，它能解决很多问题。

> * 关于在线训练平台。UP个人推荐Kaggle。原因是`每周`有30小时的免费的T4(16G)x2的GPU使用，需要注册并完成手机号认证(认证时候中国手机记着加上86)。另外提醒，数据特别敏感的个人或者企业用户请自己花钱租用服务器。

## 1. Prepare the Environment

In [ ]:
# Reference https://colab.research.google.com/drive/1Ys44kVvmeZtnICzWz0xgpRnrIOjZAuxp?usp=sharing#scrollTo=FqfebeAdT073
# 参考文献

* Unsloth supports Llama, Mistral, Phi-3, Gemma, Yi, DeepSeek, Qwen, TinyLlama, Vicuna, Open Hermes etc
* Unsloth supports 16bit LoRA or 4bit QLoRA. Both 2x faster.
* With [PR 26037](https://github.com/huggingface/transformers/pull/26037), we support downloading 4bit models **4x faster**! [Our repo](https://huggingface.co/unsloth) has Llama, Mistral 4bit models.

In [ ]:
# Modified Auther NathMath, open-sourced with Apache-2.0 Licence
# 修改作者：NathMath，以Apache-2.0 Licence许可证开源

In [1]:
# Use Multi-GPUs if available
# 可行时使用双CPU，适用于Kaggle T4x2

import os
os.environ["CUDA_VISIBLE_DEVICES"] = "0,1"
print("Completed")

Completed


In [2]:
# Install or import unsloth
# 安装或导入用于微调的unsloth库
!pip install unsloth=="2025.3.18"

# It is slow; so be patient
# 这一步很慢请耐心等待

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 46.2/46.2 kB 2.0 MB/s eta 0:00:00
INFO: pip is looking at multiple versions of torchvision to determine which version is compatible with other requirements. This could take a while.
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 192.5/192.5 kB 8.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 10.4/10.4 MB 85.9 MB/s eta 0:00:00:00:01:01
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 481.2/481.2 kB 32.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 253.1/253.1 MB 6.9 MB/s eta 0:00:000:00:0100:01
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 318.9/318.9 kB 24.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 127.8/127.8 kB 9.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 43.3/43.3 MB 41.7 MB/s eta 0:00:00:00:0100:01
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 766.7/766.7 MB 2.1 MB/s eta 0:00:000:00:0100:01
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 363.4/363.4 MB 1.9 MB/s eta 0:00:000:00:0100

In [ ]:
# DO NOT CARE BUG "ERROR: pip's dependency resolver does not currently take into account"
# 这个报错不用管：“ERROR: pip's dependency resolver does not currently take into account”

In [3]:
# Import torch backend
# 导入torch后端
import torch

torch_version = torch.cuda.get_device_capability()
torch_major_v, torch_minor_v = torch_version
print(torch_major_v, torch_minor_v)
# The first version digit must be greater or equal to 7, or a bug will be raised
# 第一个数大版本必须为7或者以上，否则会提示CUDA运算版本不足bug

# If an error is thrown here, then it means you DO NOT have a valid NVIDIA accelerator
# 如果这里报错，那么意味着你没有一个有效的NVIDIA显卡作为运算加速器，请选择T4x2而不是P100，P100会提示版本不足

7 5


In [4]:
# Install other dependences
# 安装其他依赖项
!pip install xformers trl peft accelerate bitsandbytes

In [5]:
# Import unsloth FastLanguageModel
# 导入FastLanguageModel
from unsloth import FastLanguageModel

🦥 Unsloth: Will patch your computer to enable 2x faster free finetuning.
Unsloth: Failed to patch Gemma3ForConditionalGeneration.
🦥 Unsloth Zoo will now patch everything to make training faster!


In [6]:
# See if both GPUs are activated
# 看看是否两个GPU都被激活了

gpu_count = torch.cuda.device_count()
print("GPU Number:", gpu_count)
for i in range(gpu_count):
    print(f"GPU {i}: {torch.cuda.get_device_name(i)}")

GPU Number: 2
GPU 0: Tesla T4
GPU 1: Tesla T4


In [8]:
# Import training utilities
# 导入其他训练工具
from trl import SFTTrainer
from transformers import TrainingArguments
from unsloth import is_bfloat16_supported

In [9]:
# Import data science packeges
# 导入数据科学使用的包
import numpy as np
import pandas as pd

In [ ]:
# By Nathmath

## 2. Configurate the underlying model

In [10]:
# HF token
# HF 的token，如果你需要把训练好的模型保存到hugging face时需要
_global_hf_token = ""

In [11]:
# Model configuration
# 模型设定
_global_model_name = "unsloth/gemma-2-9b-bnb-4bit"    # HF 模型识别名称
_global_model_max_seqlen = 2048                       # 模型的最长输出tokens数，小说设置到8192，但显著增加训练时间
_global_model_dtype = None
_global_model_load_in_4bit = True


In [12]:
# Model training seed configuration
# 模型训练时的种子，随机生成一个，你也可以自己设定一个
_train_seed = int(np.random.rand() * 2 ** 32)
_train_seed

1525629678

## 2.1. Load the base model into the environment

In [13]:
# Load the pretrained model
# 导入HF上预训练好的底模
_global_model, _global_tokenizer = FastLanguageModel.from_pretrained(
    model_name=_global_model_name,
    max_seq_length=_global_model_max_seqlen,
    dtype = _global_model_dtype,
    load_in_4bit = _global_model_load_in_4bit
)
# You must see Tesla T4. Num GPUs = 2. here, or you only have 1 GPU
# 在这里你必须看到GPU数量=2否则你只有1个GPU，训练会慢很多

==((====))==  Unsloth 2025.3.18: Fast Gemma2 patching. Transformers: 4.51.0.
   \\   /|    Tesla T4. Num GPUs = 2. Max memory: 14.741 GB. Platform: Linux.
O^O/ \_/ \    Torch: 2.6.0+cu124. CUDA: 7.5. CUDA Toolkit: 12.4. Triton: 3.2.0
\        /    Bfloat16 = FALSE. FA [Xformers = 0.0.29.post3. FA2 = False]
 "-____-"     Free license: http://github.com/unslothai/unsloth
Unsloth: Fast downloading is enabled - ignore downloading bars which are red colored!


model.safetensors:   0%|          | 0.00/6.13G [00:00<?, ?B/s]

generation_config.json:   0%|          | 0.00/190 [00:00<?, ?B/s]

tokenizer_config.json:   0%|          | 0.00/46.4k [00:00<?, ?B/s]

tokenizer.model:   0%|          | 0.00/4.24M [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/636 [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/17.5M [00:00<?, ?B/s]

adapter_model.safetensors:   0%|          | 0.00/432M [00:00<?, ?B/s]

Unsloth 2025.3.18 patched 42 layers with 42 QKV layers, 42 O layers and 42 MLP layers.


In [ ]:
# Patch the model and enable LoRA adapters
# 设置模型补丁：你要怎么选择训练参数
_global_model = FastLanguageModel.get_peft_model(
    _global_model,
    r = 32,                 # 选择任何大于0 的数，建议16或32或64，过大容易过拟合，且会很慢
    target_modules = ["q_proj", "k_proj", "v_proj", "o_proj", "gate_proj", "up_proj", "down_proj",],
    lora_alpha = 16,        # 同上，建议选择16或者32
    lora_dropout = 0,       # 建议选择0加速，或者0.1略微进行正则化防止过拟合
    bias = "none",
    use_gradient_checkpointing = "unsloth",
    random_state = _train_seed,
    use_rslora = False,     # True以开启rank stabilized LoRA，建议选False
    loftq_config = None,
    # Unsloth有LoRA adapters技术，因此不用训练整个模型，仅仅训练1~10%的层左右
)

In [38]:
# Standard Alpaca Prompt formatting template
# 标准Alpaca提示词模板
alpaca_prompt = """{}

### Instruction:
{}

### Response:
{}

"""
alpaca_prompt_infer = """{}

### Instruction:
{}

### Response:
"""
# {}0: System Prompt 系统提示词
# {}1: User Prompt 用户提示词
# {}2: Assistant Response 智能助理回复

# Must add EOS_TOKEN
EOS_TOKEN = _global_tokenizer.eos_token

# Formatting prompts for training
def formatting_prompts(query):
    system    = query["system"]
    instructions = query["user"]
    outputs   = query["assistant"]
    texts = []
    for syst, usr, assit in zip(system, instructions, outputs):
        # Process \n\n to \n to avoid alpaca issues
        syst = syst.replace("\n\n", "\n") if syst is not None else ""
        usr = usr.replace("\n\n", "\n")
        assit = assit.replace("\n\n", "\n")

        # Must add EOS_TOKEN, otherwise your generation will go on forever!
        text = alpaca_prompt.format(syst, usr, assit) + EOS_TOKEN
        texts.append(text)
    return { "formatted" : texts, }


In [35]:
# Load your local dataset
# 加载你的dataset(替换成你的csv文件)
from datasets import load_dataset

# Replace this by your remote file
# 替换这个链接为你的github/huggingface数据文件，建议使用csv/parq
url = r"https://huggingface.co/DOFOFFICIAL/NathUI-Tutorial/resolve/main/dataset/TrainGemma2.gameintro.queries.v2.lf.csv"
dataset = load_dataset("csv", data_files=url, split = "train")

Generating train split: 0 examples [00:00, ? examples/s]

In [36]:
# See what is it like
# 看看加载的数据是否正确
dataset[495]

{'Unnamed: 0': '173_0',
 'system': '你是一个游戏剧情规划师。',
 'user': '请根据游戏名编写游戏介绍：【游戏名】：Marguerite Sphere -マーガレット スフィア-。',
 'assistant': '真要用最简洁语言来形容这城镇的话，那就是『花之街』。\n这是充满异国情调的港口城市——白美根。\n在这所到之处皆是野生雏菊的城镇里，有着一个传说。\n——在拥有纯粹专一思念的少年少女面前，花之精灵将为他们送上，能够实现愿望的雏菊之花——\n如此的白美根街住着一对双胞胎兄妹——此花大地、此花茉莉，如今他们都在私立白美根学园上学。\n妹妹成绩优秀、头脑清晰，还有着能让学校男生们都为之着迷的可爱容貌。\n可惜的是，与那容貌相对的，她却是不管对方是谁都尖酸刻薄相待的冰山利刃。\n也正是这巨大反差，让她成为了备受他人注目的存在。\n然而，其实她只是异常腼腆，以至于没能好好表现自己，着实楚楚可怜的妹妹罢了。\n这样的她和哥哥大地，就在朋友们的簇拥下过着轻松明快的每一天。\n那样的日子，想必会一直持续下去。没错，一直持续，直到今天……\n「你还真是百年难得一遇的女难相呀……」\n这些话出自于一位无意间碰到却被硬拉着占卜的占卜师之口。\n在这点缀着纯白花朵的城镇里，如梦似幻又稍稍不可思议的恋爱故事就此拉开序幕……'}

In [39]:
# Map the training data into the formatted strings
# 将你的原始数据转化为Alpaca格式化数据
dataset_format = dataset.map(formatting_prompts, batched = True,)

Map:   0%|          | 0/28599 [00:00<?, ? examples/s]

In [40]:
# See what is it like again
# 看看格式化后的数据是否正确
dataset_format[495]

{'Unnamed: 0': '173_0',
 'system': '你是一个游戏剧情规划师。',
 'user': '请根据游戏名编写游戏介绍：【游戏名】：Marguerite Sphere -マーガレット スフィア-。',
 'assistant': '真要用最简洁语言来形容这城镇的话，那就是『花之街』。\n这是充满异国情调的港口城市——白美根。\n在这所到之处皆是野生雏菊的城镇里，有着一个传说。\n——在拥有纯粹专一思念的少年少女面前，花之精灵将为他们送上，能够实现愿望的雏菊之花——\n如此的白美根街住着一对双胞胎兄妹——此花大地、此花茉莉，如今他们都在私立白美根学园上学。\n妹妹成绩优秀、头脑清晰，还有着能让学校男生们都为之着迷的可爱容貌。\n可惜的是，与那容貌相对的，她却是不管对方是谁都尖酸刻薄相待的冰山利刃。\n也正是这巨大反差，让她成为了备受他人注目的存在。\n然而，其实她只是异常腼腆，以至于没能好好表现自己，着实楚楚可怜的妹妹罢了。\n这样的她和哥哥大地，就在朋友们的簇拥下过着轻松明快的每一天。\n那样的日子，想必会一直持续下去。没错，一直持续，直到今天……\n「你还真是百年难得一遇的女难相呀……」\n这些话出自于一位无意间碰到却被硬拉着占卜的占卜师之口。\n在这点缀着纯白花朵的城镇里，如梦似幻又稍稍不可思议的恋爱故事就此拉开序幕……',
 'formatted': '你是一个游戏剧情规划师。\n\n### Instruction:\n请根据游戏名编写游戏介绍：【游戏名】：Marguerite Sphere -マーガレット スフィア-。\n\n### Response:\n真要用最简洁语言来形容这城镇的话，那就是『花之街』。\n这是充满异国情调的港口城市——白美根。\n在这所到之处皆是野生雏菊的城镇里，有着一个传说。\n——在拥有纯粹专一思念的少年少女面前，花之精灵将为他们送上，能够实现愿望的雏菊之花——\n如此的白美根街住着一对双胞胎兄妹——此花大地、此花茉莉，如今他们都在私立白美根学园上学。\n妹妹成绩优秀、头脑清晰，还有着能让学校男生们都为之着迷的可爱容貌。\n可惜的是，与那容貌相对的，她却是不管对方是谁都尖酸刻薄相待的冰山利刃。\n也正是这巨大反差，让她成为了备受他人注目的存在。\n然而，其实她只是异常腼腆，以至于没能好好表现自己，着实楚楚

In [41]:
# Shuffle the dataset for randomness

shuffled_dataset = dataset_format.shuffle(seed = int(np.random.rand() * 2 ** 32))
shuffled_dataset

Dataset({
    features: ['Unnamed: 0', 'system', 'user', 'assistant', 'formatted'],
    num_rows: 28599
})

## 4. Train the model

In [42]:
# Configurate the model to train
# 设置你训练模型的训练参数
trainer = SFTTrainer(
    model = _global_model,
    tokenizer = _global_tokenizer,
    train_dataset = shuffled_dataset,      # 这是你formatted格式化后，shuffle后的数据
    dataset_text_field = "formatted",      # 这个字段需要与之前format函数中新建的字段保持一致
    max_seq_length = _global_model_max_seqlen,
    dataset_num_proc = 4,                  # 建议设置为4如果你使用的是colab或者kaggle
    packing = False,
    args = TrainingArguments(
        per_device_train_batch_size = 3,   # 每一个GPU训练的batchsize，建议设置为2或4或8如果你使用的是colab或者kaggle
                                           # * 这是最推荐你们微调的参数，如果你的底模很大，选择更小的值；反之亦然
                                           # * 如果提示爆显存了，那么设置成更小的值；但是，过小的值会使得训练变慢
        gradient_accumulation_steps = 10,  # 梯度累积的步数，建议设置为4或8或10，8会使得梯度更稳定，4会防止局部鞍点，不能过高，否则梯度调整次数不够
        warmup_steps = 5,
        num_train_epochs = 1,              # 微调一个epoch，一般足够了，如果你的数据集特别特殊且样本量较小，设为2
        learning_rate = 15e-5,             # 学习率，设置较低的值防止过拟合，不能过低，否则会陷入局部鞍点
                                           # * 这是第二推荐你们微调的参数，如果你的数据是正常数据，约有大几千或者几万个，1e-4是推荐的值
                                           # * 如果你的数据样本量很小，或者格式/语言并非常规的，可以考虑使用更大的值，但是封顶建议2e-4
                                           # * 此外，如果你的batch_size设置的较大，等效learning_rate会降低，因此也建议选更大的值
        fp16 = not is_bfloat16_supported(),
        bf16 = is_bfloat16_supported(),
        logging_steps = 1,
        optim = "adamw_8bit",
        weight_decay = 0.001,              # L2正则化，UP试了很久，不建议设置太大，否则会丢模型原始数据
        lr_scheduler_type = "linear",
        seed = _train_seed,
        output_dir = "outputs",
        report_to = "none",
        dataloader_num_workers = 4,      
        # If using multi-GPUS set these, 如果使用了多GPU，保留下面的内容否则注释掉
        dataloader_pin_memory = True,
        local_rank = -1, 
        ddp_find_unused_parameters = False,
    ),
)

Unsloth: Tokenizing ["formatted"] (num_proc=4):   0%|          | 0/28599 [00:00<?, ? examples/s]

In [43]:
# GPU Stats, code is provided by unsloth
# GPU数据，代码由unsloth提供
gpu_stats = torch.cuda.get_device_properties(0)
start_gpu_memory = round(torch.cuda.max_memory_reserved() / 1024 / 1024 / 1024, 3)
max_memory = round(gpu_stats.total_memory / 1024 / 1024 / 1024, 3)
print(f"GPU = {gpu_stats.name}. Max memory = {max_memory} GB.")
print(f"{start_gpu_memory} GB of memory reserved.")

GPU = Tesla T4. Max memory = 14.741 GB.
7.486 GB of memory reserved.


## 5. Train

In [ ]:
## Officially train the model
## 正式开始训练你的模型，耗费时间（几十分钟到数小时）
trainer_stats = trainer.train()
print("Completed.")

# 什么时候停止？如果你的学习率太大，几十步loss损失函数就到0.8/0.6这个位置了，那么
# 哪怕训练数据没用完，停！ 因为接下来的都是过拟合(最简单的理解就是只会照猫画虎，不会举一反三)，训练loss不是越低越好。
# 此时，自己测试一下，如果满意，导出保存。
# 如果不满意，调低一点learning_rate，再从头训练。
# 此外，如果你们的数据集中有大量数据重复或者高度相似，也有可能很快过拟合，请考虑数据集的问题。
#
# 你们一般不会见到欠拟合的情况。我也不用多说。当然如果真遇到了，再跑一次这一行代码就可以。
# 个人建议最终停止的位置是loss函数稳定到0.8 ~ 1.4之间的某一个阶段，例如已经稳定了30steps。
# 如果你们愿意略微调整一下模型而严格防止过拟合，那么可以再1.4 ~ 1.8左右停止训练，或者增加weight_decay。

==((====))==  Unsloth - 2x faster free finetuning | Num GPUs used = 1
   \\   /|    Num examples = 28,599 | Num Epochs = 1 | Total steps = 476
O^O/ \_/ \    Batch size per device = 6 | Gradient accumulation steps = 10
\        /    Data Parallel GPUs = 1 | Total batch size (6 x 10 x 1) = 60
 "-____-"     Trainable parameters = 108,036,096/9,000,000,000 (1.20% trained)


Unsloth: Will smartly offload gradients to save VRAM!


In [ ]:
# Show final training stats，code is provided by unsloth
# 训练的统计数据，代码由unsloth提供
used_memory = round(torch.cuda.max_memory_reserved() / 1024 / 1024 / 1024, 3)
used_memory_for_lora = round(used_memory - start_gpu_memory, 3)
used_percentage = round(used_memory         /max_memory*100, 3)
lora_percentage = round(used_memory_for_lora/max_memory*100, 3)
print(f"{trainer_stats.metrics['train_runtime']} seconds used for training.")
print(f"{round(trainer_stats.metrics['train_runtime']/60, 2)} minutes used for training.")
print(f"Peak reserved memory = {used_memory} GB.")
print(f"Peak reserved memory for training = {used_memory_for_lora} GB.")
print(f"Peak reserved memory % of max memory = {used_percentage} %.")
print(f"Peak reserved memory for training % of max memory = {lora_percentage} %.")

## 6. Inference Test

In [ ]:
# Reload the model, if you enter for the second time
# 重新加载模型，如果你保存了然后第二次进来
if False:
    from unsloth import FastLanguageModel

    _global_model, _global_tokenizer = FastLanguageModel.from_pretrained(
        model_name="my_gameintro_gemma9b",
        max_seq_length=_global_model_max_seqlen,
        dtype = _global_model_dtype,
        load_in_4bit = _global_model_load_in_4bit
    )


In [ ]:
# If you plan to infer rather than continue to train, call this
# 如果你希望推理而不是继续训练，调用如下这行代码，训练一定不要调
if False:
    FastLanguageModel.for_inference(_global_model)  # Enable native 2x faster inference

In [ ]:
# Inference
# 推理测试
FastLanguageModel.for_inference(_global_model)
inputs = _global_tokenizer(
[
    # Use Infer when doing inference
    alpaca_prompt_infer.format(
        "你是一个游戏剧情规划师。请你根据我提供的游戏名和游戏特色规划剧情，写出一段引人入胜的游戏介绍。", # system
        "请根据游戏名编写游戏介绍：【游戏名】：在终焉的世界里寻找盛开的花。", # input
        "", # output - 留空等待AI生成
    )
], return_tensors = "pt").to("cuda")

outputs = _global_model.generate(**inputs, max_new_tokens = 256, use_cache = 2048)
_global_tokenizer.batch_decode(outputs)

In [ ]:
# Inference in stream mode
# 流式推理测试
FastLanguageModel.for_inference(_global_model)
inputs = _global_tokenizer(
[
    # Use Infer when doing inference
    alpaca_prompt_infer.format(
        "你是一个游戏剧情规划师。请你根据我提供的游戏名和游戏特色规划剧情，写出一段引人入胜的游戏介绍。", # system
        "请根据游戏名和游戏特色编写游戏介绍：【游戏名】：风陇之歌 ~Tracking the footprints of time~，【游戏特色】：奇幻， 哲学， 冒险， 宗教， 神话， 白毛。", # input
        "", # output - 留空等待AI生成
    )
], return_tensors = "pt").to("cuda")

from transformers import TextStreamer
text_streamer = TextStreamer(_global_tokenizer)
_ = _global_model.generate(**inputs, streamer = text_streamer, max_new_tokens = 2048)

## 7. Save the model

In [ ]:
# Save model as the native huggingface version - local
# 保存模型为原生的huggingface模型到本地
_global_model.save_pretrained("my_gameintro_gemma9b")
_global_tokenizer.save_pretrained("my_gameintro_gemma9b")

# Save the merged - locel
# 保存融合的模型(包括底模)到本地
_global_model.save_pretrained_merged("my_gameintro_gemma9b_merged", _global_tokenizer, save_method = "merged_16bit",)

In [ ]:
# Save model as the native huggingface version - hf, costs time
# 保存模型为原生的huggingface模型到hf模型站，消耗时间！请为你的运行时留足时间
_global_model.push_to_hub("DOFOFFICIAL/NathUI-Tutorial", token = "hf_...")
_global_tokenizer.push_to_hub("DOFOFFICIAL/NathUI-Tutorial", token = "hf_...") 

# Save the merged - hf, costs time
# 保存融合的模型(包括底模)到hf模型站，消耗时间！请为你的运行时留足时间
_global_model.push_to_hub_merged("DOFOFFICIAL/NathUI-Tutorial", _global_tokenizer, save_method = "merged_16bit", token = "hf_...")

In [ ]:
# Save as quanted, costs time
# 保存为量化后的模型，消耗时间！请为你的运行时留足时间

# Save to Q8_0
# 保存为量化的gguf Q8_0
# _global_model.save_pretrained_gguf("my_gameintro_gemma9b_Q8_0", _global_tokenizer, quantization_method = "q8_0")
_global_model.push_to_hub_gguf("DOFOFFICIAL/ThisIsTmp", _global_tokenizer, quantization_method = "q8_0", token = "hf_...")

# Save to Q4_K_M
# 保存为量化的gguf Q4_K_M
# _global_model.save_pretrained_gguf("my_gameintro_gemma9b_Q4_K_M", _global_tokenizer, quantization_method = "q4_K_M")
_global_model.push_to_hub_gguf("DOFOFFICIAL/ThisIsTmp", _global_tokenizer, quantization_method = "q4_K_M", token = "hf_...")


In [ ]:
# Modified Auther NathMath, open-sourced with Apache-2.0 Licence
# 修改作者：NathMath，以Apache-2.0 Licence许可证开源